# Machine Translation using OpenNMT
> reference: https://github.com/Parkchanjun/SKC_MachineTranslation

# Git Clone
> or download zip file from the web site

In [9]:
!git clone https://github.com/OpenNMT/OpenNMT-py/tree/legacy.git

Cloning into 'legacy'...
fatal: repository 'https://github.com/OpenNMT/OpenNMT-py/tree/legacy.git/' not found


# Install OpenNMT

> run the below code to install OpenNMT library version <br/>
or run the setup.py from the zip data




In [2]:
!pip install OpenNMT-py==1.1.1

Looking in indexes: http://ftp.daumkakao.com/pypi/simple
     |████████████████████████████████| 189 kB 19.9 MB/s eta 0:00:01
     |████████████████████████████████| 53 kB 15.0 MB/s eta 0:00:01
     |████████████████████████████████| 47 kB 37.6 MB/s eta 0:00:01
  Attempting uninstall: tqdm
    Found existing installation: tqdm 4.42.1
    Uninstalling tqdm-4.42.1:
      Successfully uninstalled tqdm-4.42.1
  Attempting uninstall: torchtext
    Found existing installation: torchtext 0.8.0
    Uninstalling torchtext-0.8.0:
      Successfully uninstalled torchtext-0.8.0
  Attempting uninstall: OpenNMT-py
    Found existing installation: OpenNMT-py 2.0.0rc2
    Uninstalling OpenNMT-py-2.0.0rc2:
      Successfully uninstalled OpenNMT-py-2.0.0rc2


In [1]:
!pip show opennmt-py

Name: OpenNMT-py
Version: 1.1.1
Summary: A python implementation of OpenNMT
Home-page: UNKNOWN
Author: None
Author-email: None
License: UNKNOWN
Location: /home/ubuntu/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages
Requires: torchtext, six, tqdm, pyyaml, waitress, tensorboard, flask, configargparse, pyonmttok, torch, future
Required-by: 


# Prepare data

In [2]:
import pandas as pd

df = pd.read_csv('/home/ubuntu/MT/news_800k.csv')
df.head()

kor  \
0    스키너가 말한 보상은 대부분 눈으로 볼 수 있는 현물이다.   
1  심지어 어떤 문제가 발생할 건지도 어느 정도 예측이 가능하다.   
2      오직 하나님만이 그 이유를 제대로 알 수 있을 겁니다.   
3    중국의 논쟁을 보며 간과해선 안 될 게 기업들의 고충이다.   
4     박자가 느린 노래는 오랜 시간이 지나 뜨는 경우가 있다.   

                                               eng  
0         Skinner's reward is mostly eye-watering.  
1             Even some problems can be predicted.  
2                  Only God will exactly know why.  
3  Businesses should not overlook China's dispute.  
4        Slow-beating songs often float over time.

- split data to 98:1:1 ratio

In [3]:
from sklearn.model_selection import train_test_split

train, test = train_test_split(df, test_size = 0.01, random_state = 1)
train, valid = train_test_split(train, test_size = 0.0101, random_state = 1)

In [4]:
print(len(train))
print(len(test))
print(len(valid))

785359
8014
8014


In [5]:
train['kor'].to_csv('/home/ubuntu/MT/OpenNMT-py/Data/src-train.txt', index = False)
train['eng'].to_csv('/home/ubuntu/MT/OpenNMT-py/Data/tgt-train.txt', index = False)
test['kor'].to_csv('/home/ubuntu/MT/OpenNMT-py/Data/src-test.txt', index = False)
test['eng'].to_csv('/home/ubuntu/MT/OpenNMT-py/Data/tgt-test.txt', index = False)
valid['kor'].to_csv('/home/ubuntu/MT/OpenNMT-py/Data/src-valid.txt', index = False)
valid['eng'].to_csv('/home/ubuntu/MT/OpenNMT-py/Data/tgt-valid.txt', index = False)

/home/ubuntu/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/ipykernel/__main__.py:1: FutureWarning: The signature of `Series.to_csv` was aligned to that of `DataFrame.to_csv`, and argument 'header' will change its default value from False to True: please pass an explicit value to suppress this warning.
  if __name__ == '__main__':
/home/ubuntu/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/ipykernel/__main__.py:2: FutureWarning: The signature of `Series.to_csv` was aligned to that of `DataFrame.to_csv`, and argument 'header' will change its default value from False to True: please pass an explicit value to suppress this warning.
  from ipykernel import kernelapp as app
/home/ubuntu/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/ipykernel/__main__.py:3: FutureWarning: The signature of `Series.to_csv` was aligned to that of `DataFrame.to_csv`, and argument 'header' will change its default value from False to True: please pass an explicit value to suppress this war

# Subword Tokenization

> We use Byte Pair Encoding(BPE) for Subword Tokenization <br/>
reference: https://www.aclweb.org/anthology/P16-1162

i => input<br>
o => Output(*.code)<br>
s => Symbol<br>

learn_bpe => make code<br>
apply_bpe => apply subwordTokenization<br>

src-train, src-valid,test => Need to apply src.code<br>
tgt-train,tgt-val => Need to apply tgt.code

In [6]:
cd /home/ubuntu/MT

/home/ubuntu/MT


In [9]:
!python OpenNMT-py/tools/learn_bpe.py -i OpenNMT-py/Data/src-train.txt -o OpenNMT-py/Data/src.code -s -1
!python OpenNMT-py/tools/learn_bpe.py -i OpenNMT-py/Data/tgt-train.txt -o OpenNMT-py/Data/tgt.code -s -1

In [12]:
!python OpenNMT-py/tools/apply_bpe.py -c OpenNMT-py/Data/src.code -i OpenNMT-py/Data/src-train.txt -o OpenNMT-py/Data/src-train-bpe.txt
!python OpenNMT-py/tools/apply_bpe.py -c OpenNMT-py/Data/src.code -i OpenNMT-py/Data/src-valid.txt -o OpenNMT-py/Data/src-val-bpe.txt
!python OpenNMT-py/tools/apply_bpe.py -c OpenNMT-py/Data/tgt.code -i OpenNMT-py/Data/tgt-train.txt -o OpenNMT-py/Data/tgt-train-bpe.txt
!python OpenNMT-py/tools/apply_bpe.py -c OpenNMT-py/Data/tgt.code -i OpenNMT-py/Data/tgt-valid.txt -o OpenNMT-py/Data/tgt-val-bpe.txt

# **Preprocess the data**

We will be working with some example data in data/ folder.

The data consists of parallel source (src) and target (tgt) data containing one sentence per line with tokens separated by a space:

1. src-train.txt

2. tgt-train.txt

3. src-val.txt

4. tgt-val.txt


Train data and validataion data are required for machine translation training.

Validation files are required and used to evaluate the convergence of the training. It usually contains no more than 5000 sentences.


> If you think about it briefly, you can specify the path of train data and validation data, and specify the path and name to save in -save_data.

> If you want to set vocab size add below command
<br>
-src_vocab_size 32000 -tgt_vocab_size 32000

The vocab size is usually 32000.

In [11]:
!python OpenNMT-py/preprocess.py -train_src OpenNMT-py/data/src-train-bpe.txt -train_tgt OpenNMT-py/data/tgt-train-bpe.txt -valid_src OpenNMT-py/data/src-val-bpe.txt -valid_tgt OpenNMT-py/data/tgt-val-bpe.txt -save_data OpenNMT-py/data/demo -src_vocab_size 32000 -tgt_vocab_size 32000

[2020-11-28 22:29:09,211 INFO] Extracting features...
[2020-11-28 22:29:09,212 INFO]  * number of source features: 0.
[2020-11-28 22:29:09,212 INFO]  * number of target features: 0.
[2020-11-28 22:29:09,212 INFO] Building `Fields` object...
/home/ubuntu/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/torchtext/data/field.py:150: UserWarning: Field class will be retired soon and moved to torchtext.legacy. Please see the most recent release notes for further information.
  warnings.warn('{} class will be retired soon and moved to torchtext.legacy. Please see the most recent release notes for further information.'.format(self.__class__.__name__), UserWarning)
/home/ubuntu/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/torchtext/data/field.py:36: UserWarning: TextMultiField class will be retired soon and moved to torchtext.legacy. Please see the most recent release notes for further information.
  warnings.warn('{} class will be retired soon and moved to torchtext.legacy. Pl

In [2]:
!python OpenNMT-py/preprocess.py -train_src OpenNMT-py/Data/src-train-bpe.txt -train_tgt OpenNMT-py/Data/tgt-train-bpe.txt -valid_src OpenNMT-py/Data/src-val-bpe.txt -valid_tgt OpenNMT-py/Data/tgt-val-bpe.txt -save_data OpenNMT-py/Data/demo -src_vocab_size 32000 -tgt_vocab_size 32000

[2020-11-28 18:45:47,760 INFO] Extracting features...
[2020-11-28 18:45:47,760 INFO]  * number of source features: 0.
[2020-11-28 18:45:47,761 INFO]  * number of target features: 0.
[2020-11-28 18:45:47,761 INFO] Building `Fields` object...
/home/ubuntu/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/torchtext/data/field.py:150: UserWarning: Field class will be retired soon and moved to torchtext.legacy. Please see the most recent release notes for further information.
  warnings.warn('{} class will be retired soon and moved to torchtext.legacy. Please see the most recent release notes for further information.'.format(self.__class__.__name__), UserWarning)
/home/ubuntu/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/torchtext/data/field.py:36: UserWarning: TextMultiField class will be retired soon and moved to torchtext.legacy. Please see the most recent release notes for further information.
  warnings.warn('{} class will be retired soon and moved to torchtext.legacy. Pl

# **Train the data(Transformer)**

https://papers.nips.cc/paper/7181-attention-is-all-you-need.pdf


> If you get GPU-related errors, try halving batch_size

**Below is the full command, and if you want to know more about it, search about Transformer.**

!python OpenNMT-py/train.py -data OpenNMT-py/data/demo -save_model OpenNMT-py/data/model/model -layers 6 -rnn_size 512 -word_vec_size 512 -transformer_ff 2048 -heads 8 -encoder_type transformer -decoder_type transformer -position_encoding -train_steps 200000 -max_generator_batches 2 -dropout 0.1 -batch_size 4096 -batch_type tokens -normalization tokens -accum_count 2 -optim adam -adam_beta2 0.998 -decay_method noam -warmup_steps 8000 -learning_rate 2 -max_grad_norm 0 -param_init 0 -param_init_glorot -label_smoothing 0.1 -valid_steps 1000 -save_checkpoint_steps 1000 -world_size 1 -gpu_rank 0  

In [3]:
!nvidia-smi

Sat Nov 28 18:48:21 2020       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 440.64       Driver Version: 440.64       CUDA Version: 10.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|===============================+======================+======================|
|   0  Quadro RTX 6000     On   | 00000000:00:06.0 Off |                    0 |
| N/A   25C    P8    13W / 250W |      0MiB / 22698MiB |      0%      Default |
+-------------------------------+----------------------+----------------------+
                                                                               
+-----------------------------------------------------------------------------+
| Processes:                                                       GPU Memory |
|  GPU  

In [4]:
!python OpenNMT-py/train.py -data OpenNMT-py/Data/demo -save_model OpenNMT-py/Data/model/model -layers 6 -rnn_size 512 -word_vec_size 512 -transformer_ff 2048 -heads 8 -encoder_type transformer -decoder_type transformer -position_encoding -train_steps 10000 -max_generator_batches 2 -dropout 0.1 -batch_size 4096 -batch_type tokens -normalization tokens -accum_count 2 -optim adam -adam_beta2 0.998 -decay_method noam -warmup_steps 8000 -learning_rate 2 -max_grad_norm 0 -param_init 0 -param_init_glorot -label_smoothing 0.1 -valid_steps 1000 -save_checkpoint_steps 1000 -world_size 1 -gpu_rank 0  

[2020-11-28 18:49:26,969 INFO]  * src vocab size = 2429
[2020-11-28 18:49:26,969 INFO]  * tgt vocab size = 180
[2020-11-28 18:49:26,969 INFO] Building model...
[2020-11-28 18:49:32,995 INFO] NMTModel(
  (encoder): TransformerEncoder(
    (embeddings): Embeddings(
      (make_embedding): Sequential(
        (emb_luts): Elementwise(
          (0): Embedding(2429, 512, padding_idx=1)
        )
        (pe): PositionalEncoding(
          (dropout): Dropout(p=0.1, inplace=False)
        )
      )
    )
    (transformer): ModuleList(
      (0): TransformerEncoderLayer(
        (self_attn): MultiHeadedAttention(
          (linear_keys): Linear(in_features=512, out_features=512, bias=True)
          (linear_values): Linear(in_features=512, out_features=512, bias=True)
          (linear_query): Linear(in_features=512, out_features=512, bias=True)
          (softmax): Softmax(dim=-1)
          (dropout): Dropout(p=0.1, inplace=False)
          (final_linear): Linear(in_features=512, out_features

[2020-11-28 18:49:33,912 INFO] number of examples: 21911
/home/ubuntu/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/torchtext/data/iterator.py:48: UserWarning: OrderedIterator class will be retired soon and moved to torchtext.legacy. Please see the most recent release notes for further information.
  warnings.warn('{} class will be retired soon and moved to torchtext.legacy. Please see the most recent release notes for further information.'.format(self.__class__.__name__), UserWarning)
/home/ubuntu/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/torchtext/data/batch.py:23: UserWarning: Batch class will be retired soon and moved to torchtext.legacy. Please see the most recent release notes for further information.
  warnings.warn('{} class will be retired soon and moved to torchtext.legacy. Please see the most recent release notes for further information.'.format(self.__class__.__name__), UserWarning)
[2020-11-28 18:49:50,307 INFO] Step 50/10000; acc:   3.89; ppl: 68.12;

[2020-11-28 19:00:45,969 INFO] Step 1950/10000; acc:  51.79; ppl:  4.14; xent: 1.42; lr: 0.00024; 12400/24728 tok/s;    673 sec
[2020-11-28 19:00:54,331 INFO] Loading dataset from OpenNMT-py/Data/demo.train.0.pt
[2020-11-28 19:00:55,414 INFO] number of examples: 21911
[2020-11-28 19:01:03,345 INFO] Step 2000/10000; acc:  52.20; ppl:  4.08; xent: 1.41; lr: 0.00025; 11208/22415 tok/s;    690 sec
[2020-11-28 19:01:03,347 INFO] Loading dataset from OpenNMT-py/Data/demo.valid.0.pt
[2020-11-28 19:01:04,376 INFO] number of examples: 8014
[2020-11-28 19:01:27,306 INFO] Validation perplexity: 21.2576
[2020-11-28 19:01:27,306 INFO] Validation accuracy: 24.6453
[2020-11-28 19:01:27,319 INFO] Saving checkpoint OpenNMT-py/Data/model/model_step_2000.pt
[2020-11-28 19:01:45,123 INFO] Step 2050/10000; acc:  53.05; ppl:  4.00; xent: 1.39; lr: 0.00025; 4789/9590 tok/s;    732 sec
[2020-11-28 19:02:01,121 INFO] Loading dataset from OpenNMT-py/Data/demo.train.0.pt
[2020-11-28 19:02:02,157 INFO] number of 

[2020-11-28 19:12:43,354 INFO] Loading dataset from OpenNMT-py/Data/demo.train.0.pt
[2020-11-28 19:12:44,580 INFO] number of examples: 21911
[2020-11-28 19:13:00,197 INFO] Step 4000/10000; acc:  73.27; ppl:  2.21; xent: 0.79; lr: 0.00049; 11235/22712 tok/s;   1407 sec
[2020-11-28 19:13:00,200 INFO] Loading dataset from OpenNMT-py/Data/demo.valid.0.pt
[2020-11-28 19:13:01,053 INFO] number of examples: 8014
[2020-11-28 19:13:23,894 INFO] Validation perplexity: 36.9444
[2020-11-28 19:13:23,894 INFO] Validation accuracy: 25.4307
[2020-11-28 19:13:23,908 INFO] Saving checkpoint OpenNMT-py/Data/model/model_step_4000.pt
[2020-11-28 19:13:43,757 INFO] Step 4050/10000; acc:  73.84; ppl:  2.17; xent: 0.77; lr: 0.00050; 4583/9111 tok/s;   1451 sec
[2020-11-28 19:13:51,812 INFO] Loading dataset from OpenNMT-py/Data/demo.train.0.pt
[2020-11-28 19:13:53,050 INFO] number of examples: 21911
[2020-11-28 19:14:01,797 INFO] Step 4100/10000; acc:  74.21; ppl:  2.15; xent: 0.77; lr: 0.00051; 10767/21600 to

[2020-11-28 19:25:01,224 INFO] Step 6000/10000; acc:  86.08; ppl:  1.52; xent: 0.42; lr: 0.00074; 12394/24787 tok/s;   2128 sec
[2020-11-28 19:25:01,225 INFO] Loading dataset from OpenNMT-py/Data/demo.valid.0.pt
[2020-11-28 19:25:02,345 INFO] number of examples: 8014
[2020-11-28 19:25:25,288 INFO] Validation perplexity: 65.8567
[2020-11-28 19:25:25,289 INFO] Validation accuracy: 25.605
[2020-11-28 19:25:25,306 INFO] Saving checkpoint OpenNMT-py/Data/model/model_step_6000.pt
[2020-11-28 19:25:43,257 INFO] Step 6050/10000; acc:  86.69; ppl:  1.49; xent: 0.40; lr: 0.00075; 4696/9290 tok/s;   2170 sec
[2020-11-28 19:25:43,593 INFO] Loading dataset from OpenNMT-py/Data/demo.train.0.pt
[2020-11-28 19:25:44,749 INFO] number of examples: 21911
[2020-11-28 19:26:01,406 INFO] Step 6100/10000; acc:  86.55; ppl:  1.50; xent: 0.40; lr: 0.00075; 10814/21881 tok/s;   2188 sec
[2020-11-28 19:26:17,818 INFO] Step 6150/10000; acc:  86.89; ppl:  1.49; xent: 0.40; lr: 0.00076; 12164/24181 tok/s;   2205 se

[2020-11-28 19:36:59,705 INFO] number of examples: 8014
[2020-11-28 19:37:22,577 INFO] Validation perplexity: 67.4516
[2020-11-28 19:37:22,578 INFO] Validation accuracy: 26.089
[2020-11-28 19:37:22,591 INFO] Saving checkpoint OpenNMT-py/Data/model/model_step_8000.pt
[2020-11-28 19:37:32,991 INFO] Loading dataset from OpenNMT-py/Data/demo.train.0.pt
[2020-11-28 19:37:34,143 INFO] number of examples: 21911
[2020-11-28 19:37:41,738 INFO] Step 8050/10000; acc:  90.91; ppl:  1.32; xent: 0.28; lr: 0.00099; 4524/9088 tok/s;   2889 sec
[2020-11-28 19:37:58,170 INFO] Step 8100/10000; acc:  90.98; ppl:  1.31; xent: 0.27; lr: 0.00098; 12210/24379 tok/s;   2905 sec
[2020-11-28 19:38:14,223 INFO] Step 8150/10000; acc:  91.25; ppl:  1.31; xent: 0.27; lr: 0.00098; 12285/24326 tok/s;   2921 sec
[2020-11-28 19:38:14,545 INFO] Loading dataset from OpenNMT-py/Data/demo.train.0.pt
[2020-11-28 19:38:15,477 INFO] number of examples: 21911
[2020-11-28 19:38:31,378 INFO] Step 8200/10000; acc:  91.35; ppl:  1.

# **Translate**

Now that you have your model, you can start translating.

-model ==> Setting your model

Output predictions into pred.txt

In [5]:
!python OpenNMT-py/translate.py -model OpenNMT-py/Data/model/model_step_10000.pt -src OpenNMT-py/Data/src-val-bpe.txt -output OpenNMT-py/Data/pred.txt -replace_unk -verbose -beam_size 1 -gpu 0

[2020-11-28 19:49:31,461 INFO] Translating shard 0.
/home/ubuntu/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/torchtext/data/example.py:52: UserWarning: Example class will be retired soon and moved to torchtext.legacy. Please see the most recent release notes for further information.
  warnings.warn('Example class will be retired soon and moved to torchtext.legacy. Please see the most recent release notes for further information.', UserWarning)
/home/ubuntu/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/torchtext/data/iterator.py:48: UserWarning: OrderedIterator class will be retired soon and moved to torchtext.legacy. Please see the most recent release notes for further information.
  warnings.warn('{} class will be retired soon and moved to torchtext.legacy. Please see the most recent release notes for further information.'.format(self.__class__.__name__), UserWarning)
/home/ubuntu/anaconda3/envs/pytorch_p36/lib/python3.6/site-packages/torchtext/data/batch.py:23: Us

[2020-11-28 19:49:33,106 INFO] 
SENT 31: ['"@@', '특@@', '히', '경@@', '찰@@', '이', '차@@', '고', '넘@@', '치@@', '는', '증@@', '거@@', '를', '무@@', '시@@', '하@@', '고@@', ',', '꿰@@', '맞@@', '추@@', '기', '한', '증@@', '거@@', '를', '찾@@', '기', '위@@', '한', '제@@', '보@@', '도', '받@@', '고', '있@@', '는', '것@@', '으@@', '로', '알@@', '려@@', '졌@@', '다@@', '.@@', '"']
PRED 31: "@@ E@@ s@@ p@@ e@@ c@@ i@@ a@@ l@@ l@@ y k@@ n@@ o@@ w@@ s h@@ a@@ v@@ e b@@ e@@ e@@ n k@@ n@@ o@@ w@@ n a@@ n@@ d f@@ i@@ n@@ d o@@ v@@ e@@ r t@@ h@@ e p@@ o@@ l@@ i@@ c@@ e@@ .@@ "
PRED SCORE: -0.0870

[2020-11-28 19:49:33,106 INFO] 
SENT 32: ['"@@', '부@@', '친@@', '의', '직@@', '장@@', '이', '있@@', '던', '중@@', '국', '쿤@@', '밍@@', '에@@', '서', '태@@', '어@@', '나@@', ',', '가@@', '계', '혈@@', '통@@', '인', '아@@', '일@@', '랜@@', '드@@', '에@@', '서', '초@@', '등', '교@@', '육@@', '을', '받@@', '은', '뒤@@', ',', '영@@', '국@@', '의', '사@@', '립@@', '명@@', '문', '이@@', '튼', '스@@', '쿨@@', '과', '케@@', '임@@', '브@@', '리@@', '지@@', '대@@', '에', '장@@', '학@@', '생@@', '으@@', '로', '입

[2020-11-28 19:49:33,760 INFO] 
SENT 61: ['넥@@', '슨@@', '이', '이@@', '미', '출@@', '시@@', '된', '지', '1@@', '0@@', '년', '이@@', '상', '지@@', '난', '자@@', '사@@', '의', 'P@@', 'C', '온@@', '라@@', '인', '게@@', '임', '4@@', '종@@', '을', '모@@', '바@@', '일', '버@@', '전@@', '으@@', '로', '탈@@', '바@@', '꿈@@', '해', '오@@', '는', '1@@', '5@@', '일@@', '부@@', '터', '부@@', '산@@', '에@@', '서', '열@@', '리@@', '는', '국@@', '제', '게@@', '임', '축@@', '제', '‘@@', '지@@', '스@@', '타', '2@@', '0@@', '1@@', '8@@', '’@@', '에@@', '서', '공@@', '개@@', '한@@', '다@@', '.']
PRED 61: "@@ I@@ n 2@@ 0@@ 1@@ 8@@ , N@@ e@@ x@@ o@@ n h@@ a@@ s a@@ l@@ r@@ e@@ a@@ d@@ y b@@ e@@ e@@ n p@@ l@@ a@@ y@@ e@@ d i@@ n G@@ a@@ m@@ e@@ s o@@ l@@ d n@@ o@@ w@@ .@@ "
PRED SCORE: -0.0849

[2020-11-28 19:49:33,760 INFO] 
SENT 62: ['공@@', '론@@', '화@@', '위', '구@@', '성@@', '이', '늦@@', '어@@', '지@@', '면@@', '서', '당@@', '장', '시@@', '급@@', '한', '건@@', '식@@', '저@@', '장@@', '소', '증@@', '설@@', '도', '늦@@', '춰@@', '질', '전@@', '망@@', '이@@', '다@@', '.']
PRED 62: I@@ t i@@ s 

[2020-11-28 19:49:34,823 INFO] 
SENT 91: ['시@@', '는', '‘@@', '세@@', '계@@', '문@@', '화@@', '유@@', '산@@', '도@@', '시', '경@@', '주@@', "'", '‘@@', '황@@', '금@@', '도@@', '시', '경@@', '주@@', "'", '‘@@', '바@@', '다@@', '의', '도@@', '시', '경@@', '주@@', "'", '‘@@', '힐@@', '링@@', '·@@', '체@@', '험@@', '도@@', '시', '경@@', '주@@', "'", '‘@@', '꽃@@', '의', '도@@', '시', '경@@', '주@@', "'", '등', '5@@', '가@@', '지', '주@@', '제@@', '로', '홍@@', '보@@', '부@@', '스@@', '를', '구@@', '성@@', '해', '적@@', '극@@', '적@@', '인', '홍@@', '보@@', '활@@', '동@@', '을', '펼@@', '쳤@@', '다@@', '.']
PRED 91: T@@ h@@ e m@@ a@@ t@@ c@@ h p@@ l@@ a@@ y@@ e@@ r@@ s a@@ r@@ o@@ u@@ n@@ d J@@ u@@ l@@ y C@@ o@@ n@@ g@@ d@@ a@@ y i@@ n G@@ a@@ m@@ e@@ s C@@ o@@ n@@ g@@ d@@ a@@ m@@ .
PRED SCORE: -0.0917

[2020-11-28 19:49:34,824 INFO] 
SENT 92: ['"@@', '당@@', '시', '전@@', '소@@', '미@@', '를', '제@@', '외@@', '한', '멤@@', '버@@', '들@@', '이', '재@@', '결@@', '합@@', '을', '논@@', '의@@', '하@@', '고', '있@@', '다@@', '는', '보@@', '도@@', '가', '나@@', '왔@@', '지@@', '만@@', ',',

[2020-11-28 19:49:35,470 INFO] 
SENT 121: ['이@@', '번', '여@@', '론@@', '조@@', '사@@', '에@@', '서', '조@@', '사@@', '대@@', '상@@', '자', '가@@', '운@@', '데', '4@@', '4@@', '%@@', '는', '메@@', '이', '총@@', '리', '이@@', '외@@', '에', '보@@', '수@@', '당', '내', '다@@', '른', '인@@', '물@@', '이', '브@@', '렉@@', '시@@', '트', '협@@', '상@@', '을', '주@@', '도@@', '해@@', '야', '한@@', '다@@', '고', '답@@', '했@@', '다@@', '.']
PRED 121: "@@ T@@ h@@ e a@@ g@@ e s@@ h@@ o@@ u@@ l@@ d b@@ e a h@@ u@@ g@@ e i@@ n a@@ n a@@ n@@ s@@ w@@ e@@ r p@@ r@@ o@@ p@@ e@@ r@@ t@@ y f@@ o@@ r t@@ h@@ e c@@ i@@ t@@ y@@ .@@ "
PRED SCORE: -0.0839

[2020-11-28 19:49:35,470 INFO] 
SENT 122: ['나@@', '름@@', '의', '탤@@', '런@@', '트@@', '십@@', '이', '있@@', '는', '분@@', '이@@', '라', '하@@', '실', '수', '있@@', '다@@', '.']
PRED 122: I@@ t c@@ a@@ n b@@ e s@@ e@@ e@@ n o@@ n@@ l@@ y t@@ r@@ a@@ n@@ s@@ f@@ e@@ r@@ s a@@ c@@ t@@ i@@ o@@ n@@ .
PRED SCORE: -0.0876

[2020-11-28 19:49:35,470 INFO] 
SENT 123: ['같@@', '은', '사@@', '무@@', '실@@', '에@@', '서', '일@@', '하@@', '는'

...

[2020-11-28 19:52:37,216 INFO] 
SENT 7891: ['비@@', '트@@', '코@@', '인', '가@@', '격@@', '은', '코@@', '인@@', '레@@', '일', '해@@', '킹', '이@@', '전@@', '인', '지@@', '난', '8@@', '일', '미@@', '국@@', '선@@', '물@@', '거@@', '래@@', '위@@', '원@@', '회@@', '(@@', 'C@@', 'F@@', 'T@@', 'C@@', ')@@', '가', '‘@@', '비@@', '트@@', '코@@', '인', '선@@', '물@@', '’', '상@@', '품@@', '의', '가@@', '격', '조@@', '작', '의@@', '혹@@', '에', '대@@', '해', '당@@', '국@@', '에@@', '서', '수@@', '사@@', '에', '착@@', '수@@', '했@@', '다@@', '는', '사@@', '실@@', '을', '밝@@', '히@@', '면@@', '서', '하@@', '락', '추@@', '세@@', '였@@', '다@@', '.']
PRED 7891: I@@ t w@@ a@@ s K@@ o@@ r@@ e@@ a@@ n p@@ l@@ a@@ y@@ e@@ r w@@ h@@ o g@@ o@@ t s@@ i@@ n@@ g@@ e@@ r o@@ n t@@ h@@ e 8@@ t@@ h@@ -@@ p@@ r@@ i@@ c@@ e@@ s@@ .
PRED SCORE: -0.0901

[2020-11-28 19:52:37,216 INFO] 
SENT 7892: ['앞@@', '으@@', '로', '남@@', '북@@', '관@@', '계@@', '가', '더@@', '욱', '개@@', '선@@', '되@@', '면', '더@@', '욱@@', '더', '쓸@@', '모@@', '가', '없@@', '어@@', '질', '처@@', '지@@', '다@@', '.']
PRED 7892: I@@ t 

[2020-11-28 19:52:38,295 INFO] 
SENT 7921: ['경@@', '비@@', '행@@', '기', '사@@', '고@@', '로', '실@@', '종@@', '된', '에@@', '밀@@', '리@@', '아@@', '노', '살@@', '라@@', '의', '주@@', '검@@', '이', '발@@', '견@@', '됐@@', '다@@', '.']
PRED 7921: A p@@ l@@ a@@ c@@ e w@@ a@@ s f@@ o@@ u@@ n@@ d o@@ u@@ t i@@ n t@@ h@@ e a@@ c@@ c@@ i@@ d@@ e@@ n@@ t l@@ i@@ v@@ e@@ d t@@ o t@@ h@@ e e@@ c@@ o@@ n@@ o@@ m@@ y@@ .
PRED SCORE: -0.0867

[2020-11-28 19:52:38,296 INFO] 
SENT 7922: ['‘@@', '운@@', '동@@', '화', '신@@', '는@@', '다@@', '고', '뭐@@', '가', '달@@', '라@@', '지@@', '냐@@', '’@@', '는', '곱@@', '지', '않@@', '은', '시@@', '선@@', '에', '“@@', '발@@', '부@@', '터', '편@@', '해@@', '야', '도@@', '민@@', '을', '위@@', '해', '더', '많@@', '이', '움@@', '직@@', '일', '수', '있@@', '다@@', '”@@', '고', '답@@', '했@@', '던', '이', '지@@', '사@@', '는', '5@@', '개@@', '월', '만@@', '에', '운@@', '동@@', '화', '밑@@', '창@@', '이', '닳@@', '아', '노@@', '조@@', '로@@', '부@@', '터', '두', '번@@', '째', '운@@', '동@@', '화@@', '를', '선@@', '물', '받@@', '았@@', '다@@', '.']
PRED 7922: "@@ F

[2020-11-28 19:52:38,307 INFO] 
SENT 7950: ['음@@', '식', '재@@', '료@@', '가', '직@@', '접', '닿@@', '는', '부@@', '분@@', '은', '스@@', '테@@', '인@@', '리@@', '스', '스@@', '틸', '재@@', '질@@', '로', '되@@', '어', '있@@', '어', '코@@', '팅@@', '이', '벗@@', '겨@@', '질', '우@@', '려@@', '가', '없@@', '고', '내@@', '구@@', '성@@', '이', '뛰@@', '어@@', '나@@', '다@@', '.']
PRED 7950: T@@ h@@ e o@@ f@@ f@@ i@@ c@@ i@@ a@@ l r@@ e@@ a@@ c@@ h@@ e@@ s i@@ s l@@ o@@ s@@ t t@@ o r@@ u@@ n a@@ n@@ d c@@ o@@ m@@ p@@ l@@ e@@ x@@ e@@ s a p@@ e@@ r@@ f@@ o@@ r@@ m@@ .
PRED SCORE: -0.0915

[2020-11-28 19:52:38,955 INFO] 
SENT 7951: ['일@@', '각@@', '에@@', '선', '홍@@', '영@@', '표', '더@@', '불@@', '어@@', '민@@', '주@@', '당', '원@@', '내@@', '대@@', '표@@', '가', '지@@', '난', '1@@', '3@@', '일', '서@@', '울@@', '에@@', '서', '열@@', '린', '한@@', '국@@', '여@@', '성@@', '경@@', '제@@', '포@@', '럼', '행@@', '사@@', '에@@', '서', '삼@@', '성@@', '을', '겨@@', '냥@@', '해', '‘@@', '협@@', '력@@', '사@@', '를', '쥐@@', '어@@', '짜@@', '고', '있@@', '다@@', '’@@', '는', '취@@', '지@@', '의', '비@

[2020-11-28 19:52:39,618 INFO] 
SENT 7981: ['나@@', '경@@', '원', '한@@', '국@@', '당', '원@@', '내@@', '대@@', '표@@', '는', '1@@', '8@@', '일', '국@@', '회@@', '에@@', '서', '열@@', '린', '원@@', '내@@', '대@@', '책@@', '회@@', '의@@', '에@@', '서', '“@@', '일@@', '정', '구@@', '역', '전@@', '체@@', '를', '문@@', '화@@', '재@@', '로', '지@@', '정@@', '했@@', '는@@', '데', '초@@', '선@@', '의@@', '원@@', '이', '하@@', '기@@', '엔', '힘', '있@@', '는', '일@@', '”@@', '이@@', '라@@', '며', '윗@@', '선', '개@@', '입', '의@@', '혹@@', '을', '제@@', '기@@', '했@@', '다@@', '.']
PRED 7981: K@@ o@@ r@@ e@@ a@@ '@@ s f@@ i@@ r@@ s@@ t p@@ o@@ s@@ i@@ t@@ i@@ o@@ n i@@ n K@@ o@@ r@@ e@@ a h@@ a@@ s o@@ p@@ e@@ n@@ e@@ d i@@ t a@@ l@@ l 1@@ 8@@ t@@ h@@ .
PRED SCORE: -0.0821

[2020-11-28 19:52:39,618 INFO] 
SENT 7982: ['김', '웅', '총@@', '장@@', '은', '“@@', '7@@', '0@@', '년', '역@@', '사@@', '를', '지@@', '닌', '두', '대@@', '학', '간@@', '의', '교@@', '류@@', '사@@', '업@@', '이', '국@@', '제@@', '화@@', '시@@', '대', '맞@@', '춤@@', '형', '인@@', '재', '양@@', '성@@', '에', '큰', '역@@', '할@@

[2020-11-28 19:52:40,142 INFO] 
SENT 8011: ['미@@', '국', '하@@', '와@@', '이@@', '에@@', '서', '출@@', '발@@', '해', '뉴@@', '욕@@', '으@@', '로', '향@@', '하@@', '던', '하@@', '와@@', '이@@', '안@@', '항@@', '공', '여@@', '객@@', '기@@', '가', '운@@', '항', '중', '기@@', '내@@', '에@@', '서', '승@@', '무@@', '원@@', '이', '비@@', '행', '중@@', '에', '돌@@', '연', '사@@', '망@@', '하@@', '는', '사@@', '건@@', '이', '발@@', '생@@', '했@@', '다@@', '.']
PRED 8011: O@@ n@@ e o@@ f t@@ h@@ e U@@ S D@@ a@@ m@@ w@@ o@@ n c@@ a@@ m@@ e i@@ n@@ s i@@ n t@@ h@@ e U@@ S d@@ e@@ p@@ e@@ n@@ d i@@ n t@@ h@@ e U@@ S@@ .
PRED SCORE: -0.1137

[2020-11-28 19:52:40,142 INFO] 
SENT 8012: ['그@@', '는', '“@@', '북@@', '한@@', '이', '올@@', '바@@', '른', '길@@', '을', '걷@@', '는@@', '다@@', '면', '(@@', '2@@', '0@@', '0@@', '2@@', '년@@', ')', '북@@', '-@@', '일', '평@@', '양@@', '선@@', '언@@', '에', '기@@', '초@@', '해', '국@@', '교@@', '를', '정@@', '상@@', '화@@', '하@@', '고', '경@@', '제', '협@@', '력@@', '을', '할', '용@@', '의@@', '가', '있@@', '다@@', '”@@', '고@@', '도', '말@@', '했@@', '다@@', 

# Detokenization

Even after the translation process is finished, it is still in a segment, so it is different from the actual sentence structure used by real people. Thus, when you perform a detoxification process, it is returned in the form of the actual sentence.

We Use "sed" for BPE Detokenization


In [7]:
!sed -i "s/@@ //g"  OpenNMT-py/Data/pred.txt

# Evaluation Using BLEU

Quantitative evaluation is performed on the sentence thus obtained. BLEU is a quantitative evaluation method for machine translation. You can see which model is superior by comparing it to the BLEU score you are comparing.

https://www.aclweb.org/anthology/P02-1040

In [10]:
!perl  OpenNMT-py/tools/multi-bleu.perl OpenNMT-py/Data/tgt-valid.txt < OpenNMT-py/Data/pred.txt

BLEU = 0.28, 23.3/3.0/0.6/0.2 (BP=0.171, ratio=0.362, hyp_len=82814, ref_len=228948)


# Conclusion
- opennmt 라이브러를 사용하면서 pytorch에서 반복적이면서 랜덤한 데이터에서 발생하던 cuda error 문제를 해결할 수 있게 되었음
- bpe 알고리즘으로 vocab을 생성, 한영 병렬 코퍼스를 이용하여 transformer 모델 학습을 시킨 결과 BLEU score 0.28이라는 를 얻음
- 토큰화를 수행하는 apply_bpe.py 코드를 수정하여 다양한 토큰화를 이용한 모델 학습이 가능할 것으로 기대됨